In [9]:
import h2o
h2o.init()
from h2o.estimators.word2vec import H2OWord2vecEstimator
from h2o.estimators.gbm import H2OGradientBoostingEstimator
from datetime import datetime
import numpy as np
import pandas as pd

Checking whether there is an H2O instance running at http://localhost:54321 ..... not found.
Attempting to start a local H2O server...
  Java Version: java version "1.8.0_333"; Java(TM) SE Runtime Environment (build 1.8.0_333-b02); Java HotSpot(TM) 64-Bit Server VM (build 25.333-b02, mixed mode)
  Starting server from /Users/abbyjohnson/opt/anaconda3/lib/python3.9/site-packages/h2o/backend/bin/h2o.jar
  Ice root: /var/folders/9n/bhx_ndf93zl1x3nwtpj0zp7m0000gn/T/tmpt_1u9pvk
  JVM stdout: /var/folders/9n/bhx_ndf93zl1x3nwtpj0zp7m0000gn/T/tmpt_1u9pvk/h2o_abbyjohnson_started_from_python.out
  JVM stderr: /var/folders/9n/bhx_ndf93zl1x3nwtpj0zp7m0000gn/T/tmpt_1u9pvk/h2o_abbyjohnson_started_from_python.err
  Server is running at http://127.0.0.1:54321
Connecting to H2O server at http://127.0.0.1:54321 ... successful.


--------------------------  ----------------------------------
H2O_cluster_uptime:         04 secs
H2O_cluster_timezone:       America/Chicago
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.36.1.1
H2O_cluster_version_age:    26 days
H2O_cluster_name:           H2O_from_python_abbyjohnson_xvc44e
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    1.772 Gb
H2O_cluster_total_cores:    8
H2O_cluster_allowed_cores:  8
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://127.0.0.1:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.9.7 final
--------------------------  ----------------------------------

In [40]:
airbnb_names_path = "../data/airbnb_listings_2021.csv"
airbnb = pd.read_csv(airbnb_names_path)


In [11]:
airbnb_names = h2o.import_file(airbnb_names_path, destination_frame = "airbnbnames",
                             header = 1)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


In [12]:
STOP_WORDS = ["w/","at","from","in","to","/","*","-","w","+","and","&", "near", "next"]

In [13]:
def tokenize(sentences, stop_word = STOP_WORDS):
    tokenized = sentences.tokenize("\\W+")
    tokenized_lower = tokenized.tolower()
    tokenized_filtered = tokenized_lower[(tokenized_lower.nchar() >= 2) | (tokenized_lower.isna()),:]
    tokenized_words = tokenized_filtered[tokenized_filtered.grep("[0-9]",invert=True,output_logical=True),:]
    tokenized_words = tokenized_words[(tokenized_words.isna()) | (~ tokenized_words.isin(STOP_WORDS)),:]
    return tokenized_words

In [21]:
def predict(airbnb_names,w2v, gbm):
    words = tokenize(h2o.H2OFrame(airbnb_names).ascharacter())
    airbnb_names_vec = w2v.transform(words, aggregate_method="AVERAGE")
    print(gbm.predict(test_data=airbnb_names_vec))

In [15]:
print("Break airbnb names into sequence of words")
words = tokenize(airbnb_names["name"])

Break airbnb names into sequence of words


In [ ]:
print("Build word2vec model")
w2v_model = H2OWord2vecEstimator(sent_sample_rate = 0.0, epochs = 10)
w2v_model.train(training_frame=words)

Build word2vec model
word2vec Model Build progress: |█████████████████████████████████████████████████| (done) 100%
Model Details
H2OWord2vecEstimator :  Word2Vec
Model Key:  Word2Vec_model_python_1652200436282_1

No model summary for this model


In [23]:
print("Sanity check - get vector for the word 'clean'")
w2v_model.find_synonyms("clean", count = 5)

Sanity check - get vector for the word 'clean'


OrderedDict([('convenient', 0.6108201146125793),
             ('environment', 0.5399686098098755),
             ('comfortable', 0.5178377032279968),
             ('cheerful', 0.5046306252479553),
             ('cute', 0.49943193793296814)])

In [47]:
print("Calculate a vector for each airbnb name")
airbnb_names_vecs = w2v_model.transform(words, aggregate_method = "AVERAGE")

Calculate a vector for each airbnb name


In [48]:
print("Prepare training&validation data (keep only names made of known words)")
valid_airbnb_names = ~ airbnb_names_vecs["C1"].isna()
data = airbnb_names[valid_airbnb_names,:].cbind(airbnb_names_vecs[valid_airbnb_names,:])
data_split = data.split_frame(ratios=[0.8])

Prepare training&validation data (keep only names made of known words)


In [49]:
print("Build a basic GBM model")
gbm_model = H2OGradientBoostingEstimator()
gbm_model.train(x = airbnb_names_vecs.names,
                y= "price", 
                training_frame = data_split[0], 
                validation_frame = data_split[1])

Build a basic GBM model
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
Model Details
H2OGradientBoostingEstimator :  Gradient Boosting Machine
Model Key:  GBM_model_python_1652126024331_6


Model Summary: 


number_of_trees  number_of_internal_trees  model_size_in_bytes  \
0               50.0                      50.0               9862.0   

   min_depth  max_depth  mean_depth  min_leaves  max_leaves  mean_leaves  
0        5.0        5.0         5.0         6.0        21.0        11.04



ModelMetricsRegression: gbm
** Reported on train data. **

MSE: 63548.62407433614
RMSE: 252.0885242813249
MAE: 96.8214342860207
RMSLE: NaN
Mean Residual Deviance: 63548.62407433614

ModelMetricsRegression: gbm
** Reported on validation data. **

MSE: 95966.48017692077
RMSE: 309.7845705920822
MAE: 101.73448832453057
RMSLE: NaN
Mean Residual Deviance: 95966.48017692077

Scoring History: 


timestamp    duration  number_of_trees  training_rmse  \
0     2022-05-09 15:10:04   0.042 sec              0.0     283.929606   
1     2022-05-09 15:10:05   0.252 sec              1.0     282.134375   
2     2022-05-09 15:10:05   0.368 sec              2.0     279.414355   
3     2022-05-09 15:10:05   0.474 sec              3.0     277.933607   
4     2022-05-09 15:10:05   0.603 sec              4.0     276.085004   
5     2022-05-09 15:10:05   0.696 sec              5.0     275.086487   
6     2022-05-09 15:10:05   0.798 sec              6.0     273.416167   
7     2022-05-09 15:10:05   0.907 sec              7.0     271.894993   
8     2022-05-09 15:10:05   1.060 sec              8.0     270.946528   
9     2022-05-09 15:10:06   1.143 sec              9.0     270.042493   
10    2022-05-09 15:10:06   1.212 sec             10.0     268.898464   
11    2022-05-09 15:10:06   1.292 sec             11.0     268.072826   
12    2022-05-09 15:10:06   1.361 sec             12.0     267.390236   
13    2022-05-09 15:10:06   1.437 sec             13.0     266.841295   
14    2022-05-09 15:10:06   1.501 sec             14.0     266.247338   
15    2022-05-09 15:10:06   1.569 sec             15.0     265.556383   
16    2022-05-09 15:10:06   1.635 sec             16.0     265.066396   
17    2022-05-09 15:10:06   1.722 sec             17.0     264.500543   
18    2022-05-09 15:10:06   1.816 sec             18.0     263.941914   
19    2022-05-09 15:10:06   1.906 sec             19.0     263.396933   

    training_mae  training_deviance  validation_rmse  validation_mae  \
0     111.576063       80616.021241       314.501139      113.196552   
1     110.457293       79599.805407       313.009403      112.032782   
2     109.251870       78072.381787       312.328964      110.975528   
3     108.339127       77247.089864       311.197426      110.174469   
4     107.506191       76222.929558       310.655190      109.397761   
5     106.700746       75672.575311       309.749319      108.658169   
6     106.124343       74756.400623       309.621665      108.316545   
7     105.306321       73926.887045       309.212738      107.652420   
8     104.749718       73412.021017       309.009172      107.178893   
9     104.271112       72922.947876       308.394593      106.748778   
10    103.738070       72306.384044       308.190388      106.247022   
11    103.214227       71863.039886       307.947984      105.771785   
12    102.805899       71497.538197       307.874581      105.429433   
13    102.427461       71204.276478       307.510835      105.133082   
14    102.050197       70887.645084       307.526005      104.934458   
15    101.742576       70520.192776       307.527597      104.792485   
16    101.523537       70260.194262       307.288571      104.662008   
17    101.242273       69960.537455       307.051798      104.472137   
18    100.923548       69665.334194       306.949496      104.215740   
19    100.702341       69377.944430       306.970209      104.115845   

    validation_deviance  
0          98910.966746  
1          97974.886210  
2          97549.381684  
3          96843.838160  
4          96506.647243  
5          95944.640513  
6          95865.575485  
7          95612.517346  
8          95486.668119  
9          95107.225209  
10         94981.315502  
11         94831.961004  
12         94786.757740  
13         94562.913807  
14         94572.244003  
15         94573.222829  
16         94426.266085  
17         94280.806933  
18         94217.992990  
19         94230.709080


See the whole table with table.as_data_frame()

Variable Importances: 


variable  relative_importance  scaled_importance  percentage
0       C27          362290912.0           1.000000    0.136884
1       C83          133559256.0           0.368652    0.050462
2       C32          131694104.0           0.363504    0.049758
3       C84          111575160.0           0.307971    0.042156
4       C51          101447688.0           0.280017    0.038330
5       C25           92763960.0           0.256048    0.035049
6       C40           86613544.0           0.239072    0.032725
7       C93           78999264.0           0.218055    0.029848
8       C10           72973032.0           0.201421    0.027571
9       C87           67833648.0           0.187235    0.025629
10      C96           67187808.0           0.185453    0.025385
11     C100           63601172.0           0.175553    0.024030
12      C55           58155104.0           0.160520    0.021973
13      C94           56120556.0           0.154905    0.021204
14      C69           56085564.0           0.154808    0.021191
15      C72           49543140.0           0.136750    0.018719
16      C85           47548580.0           0.131244    0.017965
17      C16           46522408.0           0.128412    0.017577
18      C15           45973784.0           0.126897    0.017370
19      C76           44062624.0           0.121622    0.016648


See the whole table with table.as_data_frame()


In [50]:
print("Predict!")
print(predict(["Cozy & Clean Apartment for Two"], w2v_model, gbm_model))
print(predict(["Private Room Near Central Park"], w2v_model, gbm_model))
print(predict(["Charming Apartment Walking Distance from Times Square"], w2v_model, gbm_model))

Predict!
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 129.15


None
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 101.527


None
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 175.202


None


In [ ]:
# trying to add w2v price predictions as a new feature in dataset

names = airbnb["name"].tolist()

airbnb_names = h2o.import_file(airbnb_names_path, destination_frame = "airbnbnames",
                             header = 1)
words = tokenize(airbnb_names["name"])
w2v_model = H2OWord2vecEstimator(sent_sample_rate = 0.0, epochs = 10)
w2v_model.train(training_frame=words)
airbnb_names_vecs = w2v_model.transform(words, aggregate_method = "AVERAGE")
valid_airbnb_names = ~ airbnb_names_vecs["C1"].isna()
data = airbnb_names[valid_airbnb_names,:].cbind(airbnb_names_vecs[valid_airbnb_names,:])
data_split = data.split_frame(ratios=[0.8])
gbm_model = H2OGradientBoostingEstimator()
gbm_model.train(x = airbnb_names_vecs.names,
                y= "price", 
                training_frame = data_split[0], 
                validation_frame = data_split[1])

w2v = []

for name in names:
    prediction = predict([name], w2v_model, gbm_model)
    w2v.append(prediction)
print(w2v)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
word2vec Model Build progress: |█████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 278.266


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 191.729


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


...


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 152.654


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict 
 
 
 159.864


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


NameError: name 'w2v' is not defined